In [53]:
# import requests

# res = requests.get('http://127.0.0.1:5005/init')
# with open("test.json", "w") as f:
#     f.write(res.json())

[{'links': [{'source': 'Person_3.0242588970131256e+18', 'target': 'Desire_3.0242588970131256e+18_Shop', 'type': 'WANT_TO'}, {'source': 'Person_1.3493719364692498e+19', 'target': 'Desire_1.3493719364692498e+19_Shop', 'type': 'WANT_TO'}, {'source': 'Person_2.917802597231933e+18', 'target': 'Desire_2.917802597231933e+18_Errands', 'type': 'WANT_TO'}, {'source': 'Person_7.586493324751371e+18', 'target': 'Desire_7.586493324751371e+18_Shop', 'type': 'WANT_TO'}, {'source': 'Person_2.628092394650728e+18', 'target': 'Desire_2.628092394650728e+18_Recreation', 'type': 'WANT_TO'}, {'source': 'Person_1.273140952659186e+18', 'target': 'Desire_1.273140952659186e+18_Eat', 'type': 'WANT_TO'}, {'source': 'Person_1.326341779854978e+19', 'target': 'Desire_1.326341779854978e+19_Eat', 'type': 'WANT_TO'}, {'source': 'Person_1.404513066245654e+19', 'target': 'Desire_1.404513066245654e+19_Eat', 'type': 'WANT_TO'}, {'source': 'Person_1.4737889322621346e+19', 'target': 'Desire_1.4737889322621346e+19_Eat', 'type':

# Prepare Behavior Graph

In [1]:
import sys
import os

sys.path.append('..')

from model import ChoiceModel

# Initialize the model, for the first time, you need to set skip_init to 'False'. it will take a while to prepare the data.
# sample_num is the total number of samples to build the dataset.

choice_model = ChoiceModel(
    data_dir='../data', desire='Eat', sample_num=100, skip_init=True, skip_test=True)

train_data_path = choice_model._prepare_train_data(
                sample_num=1000, desire=None)
choice_model._prepare_neo4j(train_data_path)

Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.FeatureDeprecationWarning} {category: DEPRECATION} {title: This feature is deprecated and will be removed in future versions.} {description: The procedure has a deprecated field. ('config' used by 'apoc.meta.graphSample' is deprecated.)} {position: line: 1, column: 1, offset: 0} for query: "CALL apoc.meta.graphSample() YIELD nodes, relationships RETURN nodes, [rel in relationships | {name:apoc.any.property(rel, 'type'), count: apoc.any.property(rel, 'count')}] AS relationships"


In [4]:
# clear similar_to edge
'''
MATCH ()-[r:SIMILAR_TO]->()
DELETE r
'''

# add similar_to edge
'''
MATCH (p:Person)
CALL {
  WITH p
  MATCH (similar:Person)
  WHERE p.id <> similar.id
  WITH p, similar, gds.similarity.cosine(p.embedding, similar.embedding) AS similarityScore
  ORDER BY similarityScore DESC
  LIMIT 5
  MERGE (p)-[r:SIMILAR_TO]->(similar)
  SET r.score = similarityScore, r.type = 'SIMILAR_TO'
  RETURN count(*) as count
}
RETURN count(p) as processedNodes
'''

"\nMATCH (p:Person)\nCALL {\n  WITH p\n  MATCH (similar:Person)\n  WHERE p.id <> similar.id\n  WITH p, similar, gds.similarity.cosine(p.embedding, similar.embedding) AS similarityScore\n  ORDER BY similarityScore DESC\n  LIMIT 5\n  MERGE (p)-[r:SIMILAR_TO]->(similar)\n  SET r.score = similarityScore, r.type = 'SIMILAR_TO'\n  RETURN count(*) as count\n}\nRETURN count(p) as processedNodes\n"

# Convert Graph Data to Json file

In [48]:
query = '''
MATCH (p:Person)
WITH p ORDER BY rand() LIMIT 1000

// Match the original relationships for the randomly selected persons
MATCH (p)-[r1:WANT_TO]->(d:Desire)-[r2:GO_TO]->(i:Intention)
OPTIONAL MATCH (p)-[r3:SIMILAR_TO]->(s:Person)

// Also match the relationships for the similar persons
OPTIONAL MATCH (s)-[r4:WANT_TO]->(sd:Desire)-[r5:GO_TO]->(si:Intention)

RETURN 
    // Collect original nodes
    COLLECT(DISTINCT p {.*, type: 'Person', id: p.id, name: p.description, embedding: null}) + 
    COLLECT(DISTINCT d {.*, type: 'Desire', id: d.id, name: d.desire, embedding: null}) + 
    COLLECT(DISTINCT i {.*, type: 'Intention', id: i.id, name: i.target_amenity, embedding: null}) +
    // Collect similar nodes
    COLLECT(DISTINCT s {.*, type: 'Person', id: d.id, name: s.description, embedding: null}) +
    COLLECT(DISTINCT sd {.*, type: 'Desire', id: sd.id, name: sd.desire, embedding: null}) +
    COLLECT(DISTINCT si {.*, type: 'Intention', id: si.id, name: si.target_amenity, embedding: null}) AS nodes,

    // Collect original links
    COLLECT(DISTINCT { source: p.id, target: d.id, type: 'WANT_TO' }) +
    COLLECT(DISTINCT { source: d.id, target: i.id, type: 'GO_TO' }) + 
    COLLECT(DISTINCT { source: p.id, target: s.id, type: 'SIMILAR_TO' }) +
    // Collect similar person links
    COLLECT(DISTINCT { source: s.id, target: sd.id, type: 'WANT_TO' }) +
    COLLECT(DISTINCT { source: sd.id, target: si.id, type: 'GO_TO' }) AS links

'''

In [49]:
query_result = choice_model._get_cypher_query(query)

In [50]:
import json 
data = {}

with open('./public/graph.json', 'w') as f:
    json.dump(query_result, f)

# Similarity Search

In [12]:

# desire can be one of 'Eat,Shop,Recreation'
desire = 'Eat'

# You can input any profile of a person, but there will be a failure chance that the model can't generate the proper cypher query, try to use the following categories will be better.

# 'income' 'Debt','Low','Moderate','High','Very High','Ultra High'
# 'age' :  'Teen' ,'Young Adult', 'Adult', 'Middle Age', 'Senior', 'Elderly'

profile = 'a young adult with high income'

In [29]:
query = f'''
MATCH (p)-[r1:WANT_TO]->(d:Desire {{desire: '{desire}'}})-[r2:GO_TO]->(i:Intention)
WITH 
    COLLECT(DISTINCT p {{.*, type: 'Person', id: p.id}}) AS person
return person
'''

query_results = choice_model._get_cypher_query(query)
query_results = choice_model._get_similar_nodes(profile, query_results,k=50)
ids = [p['id'] for p in query_results]

Received notification from DBMS server: {severity: WARNING} {code: Neo.ClientNotification.Statement.FeatureDeprecationWarning} {category: DEPRECATION} {title: This feature is deprecated and will be removed in future versions.} {description: The query used a deprecated procedure. ('db.create.setVectorProperty' has been replaced by 'db.create.setNodeVectorProperty')} {position: line: 1, column: 80, offset: 79} for query: "UNWIND $data AS row CALL { WITH row MERGE (c:`Chunk` {id: row.id}) WITH c, row CALL db.create.setVectorProperty(c, 'embedding', row.embedding) YIELD node SET c.`text` = row.text SET c += row.metadata } IN TRANSACTIONS OF 1000 ROWS"


In [41]:
query = f'''
MATCH (p:Person)
WHERE p.id IN {ids}
MATCH (p)-[r1:WANT_TO]->(d:Desire {{desire: '{desire}'}})-[r2:GO_TO]->(i:Intention)
MATCH (p)-[r3:SIMILAR_TO]->(s:Person)
MATCH (s)-[r4:WANT_TO]->(sd:Desire {{desire: '{desire}'}})-[r5:GO_TO]->(si:Intention)

WITH 
    // Collect original links
    COLLECT(DISTINCT {{ source: p.id, target: d.id, type: 'WANT_TO' }}) + 
    COLLECT(DISTINCT {{ source: d.id, target: i.id, type: 'GO_TO' }}) +
    COLLECT(DISTINCT {{ source: p.id, target: s.id, type: 'SIMILAR_TO' }}) +
    // Collect similar person links
    COLLECT(DISTINCT {{ source: s.id, target: sd.id, type: 'WANT_TO' }}) +
    COLLECT(DISTINCT {{ source: sd.id, target: si.id, type: 'GO_TO' }}) 
    AS links,

    // Collect original and similar nodes
    COLLECT(DISTINCT p {{.*, type: 'Person', id: p.id, name: p.description, embedding: null}}) + 
    COLLECT(DISTINCT d {{.*, type: 'Desire', id: d.id, name: d.desire, embedding: null}}) + 
    COLLECT(DISTINCT i {{.*, type: 'Intention', id: i.id, name: i.description, embedding: null}}) + 
    COLLECT(DISTINCT s {{.*, type: 'Person', id: s.id, name: s.description, embedding: null}}) +
    COLLECT(DISTINCT sd {{.*, type: 'Desire', id: sd.id, name: sd.desire, embedding: null}}) +
    COLLECT(DISTINCT si {{.*, type: 'Intention', id: si.id, name: si.description, embedding: null}}) 
    AS nodes

WITH 
    nodes, links,

    // Extract IDs of linked nodes
    [l IN links | l.source] + [l IN links | l.target] AS linked_node_ids

// Filter out isolated nodes
WITH [n IN nodes WHERE n.id IN linked_node_ids] AS filtered_nodes, links

RETURN filtered_nodes AS nodes, links
'''

In [42]:
query_result = choice_model._get_cypher_query(query)

In [43]:
import json 
import uuid

agent_id = str(uuid.uuid4())
node_ids = [n['id'] for n in query_result['nodes']]
query_result['nodes'].append({
    'id': agent_id,
    'name': profile,
    'type': 'Agent',
})
for id in ids:
    if id in node_ids:
        query_result['links'].append({
            'source': agent_id,
            'target': id,
            'type': 'SIMILAR_TO'
        })
with open('./public/graph.json', 'w') as f:
    json.dump(query_result, f)

In [39]:
intentions = [n for n in query_result['nodes'] if n['type'] == 'Intention']
print(len(intentions))

99


In [40]:
intentions[0]

{'id': 'Internsion_1.6288949837444995e+19',
 'location_name': 'Trade',
 'description': 'This person goes to Trade by Walking, this place is in the amenity category of F&B Eatery/Full-Service Restaurants. The distance is 0.0797343266858613 miles. It takes 1.0 minutes.',
 'name': 'F&B Eatery/Full-Service Restaurants by Walking',
 'embedding': None,
 'type': 'Intention',
 'target_amenity': 'F&B Eatery/Full-Service Restaurants',
 'duration_minutes': 1.0,
 'mode': 'Walking',
 'distance_miles': 0.0797343266858613}

In [44]:
from collections import Counter
amenity_choices = [i['target_amenity'] for i in intentions]
mobility_choices = [i['mode'] for i in intentions]

amenity_counter = Counter(amenity_choices)
mobility_counter = Counter(mobility_choices)
print("Amenity Choices Count:", amenity_counter)
print("Mobility Choices Count:", mobility_counter)

Amenity Choices Count: Counter({'F&B Eatery/Full-Service Restaurants': 52, 'F&B Eatery/Snack and Nonalcoholic Beverage Bars': 21, 'F&B Eatery/Limited-Service Restaurants': 19, 'F&B Eatery/Drinking Places': 7})
Mobility Choices Count: Counter({'Walking': 47, 'Public_transport': 28, 'Car': 24})


In [45]:
data = []
for k,v in amenity_counter.items():
    data.append({"name":k, "value":v})
print(data)

[{'name': 'F&B Eatery/Full-Service Restaurants', 'value': 52}, {'name': 'F&B Eatery/Snack and Nonalcoholic Beverage Bars', 'value': 21}, {'name': 'F&B Eatery/Drinking Places', 'value': 7}, {'name': 'F&B Eatery/Limited-Service Restaurants', 'value': 19}]


In [47]:
data = []
for k,v in amenity_counter.items():
    data.append({"state":k, "value":v})
print(data)

[{'state': 'F&B Eatery/Full-Service Restaurants', 'value': 52}, {'state': 'F&B Eatery/Snack and Nonalcoholic Beverage Bars', 'value': 21}, {'state': 'F&B Eatery/Drinking Places', 'value': 7}, {'state': 'F&B Eatery/Limited-Service Restaurants', 'value': 19}]
